# Learning CNN with MNIST

In [1]:
!pip install tensorflowjs

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 89.1/89.1 kB 2.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.0/53.0 kB 5.1 MB/s eta 0:00:00
  Attempting uninstall: packaging
    Found existing installation: packaging 25.0
    Uninstalling packaging-25.0:
      Successfully uninstalled packaging-25.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
xarray 2025.12.0 requires packaging>=24.1, but you have packaging 23.2 which is incompatible.
google-cloud-bigquery 3.40.0 requires packaging>=24.2.0, but you have packaging 23.2 which is incompatible.
db-dtypes 1.5.0 requires packaging>=24.2.0, but you have packaging 23.2 which is incompatible.


## Loading and understanding data







In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import seaborn as sns

import tensorflow as tf
from tensorflow.keras.models import Sequential, Model
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, Dropout, Input
from sklearn.metrics import confusion_matrix

In [ ]:
(x_train, y_train), (x_test, y_test) = tf.keras.datasets.mnist.load_data()

In [ ]:
# Check shapes of the datasets
print(f"x_train shape: {x_train.shape}")
print(f"y_train shape: {y_train.shape}")
print(f"x_test shape: {x_test.shape}")
print(f"y_test shape: {y_test.shape}")

In [ ]:
# Check unique values in target variables
print(f"Unique values in y_train: {np.unique(y_train)}")
print(f"Unique values in y_test: {np.unique(y_test)}\n")

## Visualizing some data




In [ ]:
plt.imshow(x_train[0], cmap='gray')
print(y_train[0])

In [ ]:
def visualize_images(data):
    fig, axes = plt.subplots(nrows=2, ncols=10, figsize=(12,3))

    for i, ax in enumerate(axes.flat):
        ax.imshow(x_train[i], cmap='gray')
        ax.set_xticks([]), ax.set_yticks([])
        ax.set_title(str(y_train[i]))

    plt.tight_layout()
    plt.show()

visualize_images(x_train)

## Normalizing data between 0 - 1

In [ ]:
x_train = x_train.astype("float32") / 255.0
x_test  = x_test.astype("float32") / 255.0

In [ ]:
x_train.shape

In [ ]:
x_train = x_train.reshape(x_train.shape[0], 28, 28, 1)
x_test = x_test.reshape(x_test.shape[0], 28, 28, 1)

print("x_train shape:", x_train.shape)
print("x_test shape:", x_test.shape)

In [ ]:
x_train.shape[1:]

## Model Building

Conv → Pool → Conv → Pool → Flatten → Dense

In [ ]:
# input shape >> (28, 28, 1)
inputs = Input(batch_shape=(None, 28, 28, 1), name='input_layer')

x = Conv2D(filters=32, kernel_size=(3,3), padding='same', activation='relu', name='conv1')(inputs)
x = Conv2D(filters=32, kernel_size=(3,3), activation='relu', name='conv2')(x)
x = MaxPooling2D(pool_size=(2,2))(x)
x = Dropout(0.25)(x)


x = Conv2D(filters=64, kernel_size=(3,3), activation='relu', name='conv3' )(x)
x = MaxPooling2D(pool_size=(2,2))(x)
x = Dropout(0.25)(x)

x = Flatten()(x)

# dense layers
x = Dense(128, activation='relu')(x)
x = Dropout(0.5)(x)
outputs = Dense(10, activation='softmax')(x)

# Create model
model = Model(inputs=inputs, outputs=outputs)

# compile
model.compile(
    optimizer='adam',
    loss='sparse_categorical_crossentropy',
    metrics=['accuracy']
)

In [ ]:
model.summary()

In [ ]:
history = model.fit(x_train, y_train, epochs=8, validation_data=(x_test, y_test))


## Train & Test Accuracy and Loss¶

In [ ]:
plt.figure(figsize=(20,6))
plt.subplot(1,2,1)
plt.plot(history.history['accuracy'], color='b', label='Training Accuracy')
plt.plot(history.history['val_accuracy'], color='r', label='Validation Accuracy')
plt.legend()
plt.xlabel('Epoch', fontsize=16)
plt.ylabel('Accuracy', fontsize=16)
plt.ylim([min(plt.ylim()),1])
plt.title('Train and Test Accuracy')
plt.grid(True)

plt.subplot(1,2,2)
plt.plot(history.history['loss'], color='b', label='Training Loss')
plt.plot(history.history['val_loss'], color='r', label='Validation Loss')
plt.legend()
plt.xlabel('Epoch', fontsize=16)
plt.ylabel('Loss', fontsize=16)
plt.ylim([0,max(plt.ylim())])
plt.title('Train and Test Loss')
plt.grid(True)
plt.show()

## Confusion Matrix

In [ ]:
y_pred = model.predict(x_test)
y_pred_classes = np.argmax(y_pred, axis=1)

cm = confusion_matrix(y_test, y_pred_classes)

plt.figure(figsize=(8,6))
sns.heatmap(cm, annot=True, fmt='d', cmap='Blues')

plt.xlabel("Predicted")
plt.ylabel("Actual")
plt.title("Confusion Matrix")
plt.show()


In [ ]:
model.predict(x_test[0].reshape(1, 28, 28, 1))

## Looking into model

In [ ]:
test_img = x_test[0].reshape(1, 28, 28, 1)

layer_names = ['conv1', 'conv2', 'conv3']
layer_outputs = [model.get_layer(name).output for name in layer_names]

# Visualization model
activation_model = Model(inputs=model.input, outputs=layer_outputs)

# Get the feature maps for the image
activations = activation_model.predict(test_img)

plt.figure(figsize=(15, 5))

for i, activation in enumerate(activations):
    plt.subplot(1, 3, i + 1)

    # We take the average of all filters (channels) to see the overall focus
    # For conv1 (32 filters), this averages those 32 images into one
    feature_map = np.mean(activation, axis=-1)

    plt.imshow(feature_map[0], cmap='viridis')
    plt.title(f"Layer: {layer_names[i]}")
    plt.axis('off')

plt.tight_layout()
plt.show()

In [ ]:
# 1. Get the activation for just the first layer (conv1)
first_layer_activation = activations[0] # From our previous activation_model.predict code

# 2. Create a 4x8 grid to show all 32 filters
plt.figure(figsize=(16, 8))

for i in range(32):
    plt.subplot(4, 8, i + 1)

    # Each filter 'i' is visualized here
    plt.imshow(first_layer_activation[0, :, :, i], cmap='viridis')
    plt.title(f"Filt {i+1}", fontsize=8)
    plt.axis('off')

plt.suptitle("Output of all 32 Filters in conv1")
plt.show()

## Export model

In [ ]:
model.build(input_shape=(None, 28, 28, 1))

# Now save and convert again
import tensorflowjs as tfjs
tfjs.converters.save_keras_model(model, 'web_model')

In [ ]:
!zip -r web_model.zip web_model
from google.colab import files
files.download("web_model.zip")

## The last way trained on locally using old tf

In [2]:
from google.colab import files
files.upload()


Saving mnist.h5 to mnist.h5


{'mnist.h5': b'\x89HDF\r\n\x1a\n\x00\x00\x00\x00\x00\x08\x08\x00\x04\x00\x10\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\xff\xff\xff\xff\xff\xff\xff\xffX\xbf+\x00\x00\x00\x00\x00\xff\xff\xff\xff\xff\xff\xff\xff\x00\x00\x00\x00\x00\x00\x00\x00`\x00\x00\x00\x00\x00\x00\x00\x01\x00\x00\x00\x00\x00\x00\x00\x88\x00\x00\x00\x00\x00\x00\x00\xa8\x02\x00\x00\x00\x00\x00\x00\x01\x00\x06\x00\x01\x00\x00\x00\x18\x00\x00\x00\x00\x00\x00\x00\x10\x00\x10\x00\x00\x00\x00\x00 \x03\x00\x00\x00\x00\x00\x00P\x01\x00\x00\x00\x00\x00\x00TREE\x00\x00\x01\x00\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\xff\x00\x00\x00\x00\x00\x00\x00\x00\x00(\x00\x00\x00\x00\x00\x00\x18\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x

In [3]:
import tensorflowjs as tfjs

!tensorflowjs_converter \
  --input_format=keras \
  mnist.h5 \
  mnist_tfjs


2026-01-22 21:58:41.317146: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1769119121.339968    1131 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1769119121.346912    1131 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1769119121.364823    1131 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1769119121.364864    1131 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1769119121.364868    1131 computation_placer.cc:177] computation placer alr